In [1]:
from transformers import pipeline
import torch
from IPython.display import Audio

device = "cuda:0" if torch.cuda.is_available() else "cpu"

classifier = pipeline(
    "audio-classification", model="MIT/ast-finetuned-speech-commands-v2", device=device
)

/home/matias/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


### Reconocer palabra para empezar

In [2]:
from transformers.pipelines.audio_utils import ffmpeg_microphone_live

print(classifier.model.config.id2label)

def launch_fn(
    wake_word="marvin",
    prob_threshold=0.5,
    chunk_length_s=2.0,
    stream_chunk_s=0.25,
    debug=False,
):
    if wake_word not in classifier.model.config.label2id.keys():
        raise ValueError(
            f"Wake word {wake_word} not in set of valid class labels, pick a wake word in the set {classifier.model.config.label2id.keys()}."
        )

    sampling_rate = classifier.feature_extractor.sampling_rate

    mic = ffmpeg_microphone_live(
        sampling_rate=sampling_rate,
        chunk_length_s=chunk_length_s,
        stream_chunk_s=stream_chunk_s,
    )

    print("Listening for wake word...")
    for prediction in classifier(mic):
        prediction = prediction[0]
        if debug:
            print(prediction)
        if prediction["label"] == wake_word:
            if prediction["score"] > prob_threshold:
                return True
            
launch_fn(debug=True)

{0: 'backward', 1: 'follow', 2: 'five', 3: 'bed', 4: 'zero', 5: 'on', 6: 'learn', 7: 'two', 8: 'house', 9: 'tree', 10: 'dog', 11: 'stop', 12: 'seven', 13: 'eight', 14: 'down', 15: 'six', 16: 'forward', 17: 'cat', 18: 'right', 19: 'visual', 20: 'four', 21: 'wow', 22: 'no', 23: 'nine', 24: 'off', 25: 'three', 26: 'left', 27: 'marvin', 28: 'yes', 29: 'up', 30: 'sheila', 31: 'happy', 32: 'bird', 33: 'go', 34: 'one'}
Listening for wake word...


/home/matias/.local/lib/python3.10/site-packages/transformers/models/audio_spectrogram_transformer/feature_extraction_audio_spectrogram_transformer.py:96: UserWarning: The given NumPy array is not writable, and PyTorch does not support non-writable tensors. This means writing to this tensor will result in undefined behavior. You may want to copy the array to protect its data or make it writable before converting it to a tensor. This type of warning will be suppressed for the rest of this program. (Triggered internally at ../torch/csrc/utils/tensor_numpy.cpp:206.)
  waveform = torch.from_numpy(waveform).unsqueeze(0)


{'score': 0.04762890934944153, 'label': 'two'}
{'score': 0.1426355093717575, 'label': 'six'}
{'score': 0.11895965784788132, 'label': 'up'}
{'score': 0.13453948497772217, 'label': 'off'}
{'score': 0.12843511998653412, 'label': 'stop'}
{'score': 0.13055971264839172, 'label': 'stop'}
{'score': 0.13055971264839172, 'label': 'stop'}
{'score': 0.13055971264839172, 'label': 'stop'}
{'score': 0.14089344441890717, 'label': 'up'}
{'score': 0.35520532727241516, 'label': 'stop'}
{'score': 0.33248171210289, 'label': 'stop'}
{'score': 0.33248171210289, 'label': 'stop'}
{'score': 0.33248171210289, 'label': 'stop'}
{'score': 0.33248171210289, 'label': 'stop'}
{'score': 0.18591004610061646, 'label': 'stop'}
{'score': 0.16003373265266418, 'label': 'stop'}
{'score': 0.16003373265266418, 'label': 'stop'}
{'score': 0.16003373265266418, 'label': 'stop'}
{'score': 0.16003373265266418, 'label': 'stop'}
{'score': 0.7757278680801392, 'label': 'marvin'}


True

### Transcribir audio

In [3]:
transcriber = pipeline(
    "automatic-speech-recognition", model="openai/whisper-base.en", device=device
)
import sys


def transcribe(chunk_length_s=5.0, stream_chunk_s=1.0):
    sampling_rate = transcriber.feature_extractor.sampling_rate

    mic = ffmpeg_microphone_live(
        sampling_rate=sampling_rate,
        chunk_length_s=chunk_length_s,
        stream_chunk_s=stream_chunk_s,
    )

    print("Start speaking...")
    for item in transcriber(mic, generate_kwargs={"max_new_tokens": 128}):
        sys.stdout.write("\033[K")
        print(item["text"], end="\r")
        if not item["partial"][0]:
            break

    return item["text"]

In [5]:
model_id = "openai/whisper-base"  # update with your model id
#model_id ="openai/whisper-tiny"
transcriber = pipeline(
        "automatic-speech-recognition",
        model =  model_id,
        max_new_tokens=256,
        generate_kwargs={
            "task": "transcribe",
            "language": "spanish",
        },  
    )

def transcribe_whisper(chunk_length_s=5.0, stream_chunk_s=1.0):
    sampling_rate = transcriber.feature_extractor.sampling_rate

    mic = ffmpeg_microphone_live(
        sampling_rate=sampling_rate,
        chunk_length_s=chunk_length_s,
        stream_chunk_s=stream_chunk_s,
    )

    print("Start speaking...")
    for item in transcriber(mic):
        sys.stdout.write("\033[K")
        print(item["text"], end="\r")
        if not item["partial"][0]:
            break

    return item["text"]
transcribe()

Start speaking...


' hola, how are you?'

In [27]:
def transcribe_speech(filepath):
    pipe = pipeline("automatic-speech-recognition", model=model_id)
    output = pipe(
        filepath,
        max_new_tokens=256,
        generate_kwargs={
            "task": "transcribe",
            "language": "spanish",
        },  # update with the language you've fine-tuned on
        chunk_length_s=30,
        batch_size=8,
    )
    return output["text"]


### Responder el mensaje

In [6]:

from huggingface_hub import HfFolder
import requests

#"tiiuae/falcon-7b-instruct"
def query(text, model_id="PulsarAI/llama-2-alpacagpt4-1000step"):
    api_url = f"https://api-inference.huggingface.co/models/{model_id}"
    headers = {"Authorization": f"Bearer {HfFolder().get_token()}"}
    payload = {"inputs": text}

    print(f"Querying...: {text}")
    response = requests.post(api_url, headers=headers, json=payload)
    # return response.json()[0]["generated_text"][len(text) + 1 :]
    return response

query("How many days are in a week?")

Querying...: How many days are in a week?


<Response [503]>

In [8]:
import os
import openai
from dotenv import load_dotenv

# Load environment variables from the .env file de forma local
load_dotenv()
openai.api_key = os.environ['OPENAI_API_KEY']

In [9]:
def query_chatgpt(text):
    messages = []
    messages.append({'role': 'user', 'content': '{}'.format(text)})
    print("Preguntando "+text)
    response = openai.ChatCompletion.create(
            model="gpt-3.5-turbo",
            messages= messages,
            temperature=0.5,
            max_tokens=120
            ).choices[0].message.content
    return response

In [10]:
query_chatgpt("hola, cómo estas?")

Preguntando hola, cómo estas?


'¡Hola! Estoy bien, gracias. ¿Y tú?'

### Generar la respuesta


#### microsoft t5

In [11]:
from transformers import SpeechT5Processor, SpeechT5ForTextToSpeech, SpeechT5HifiGan

processor = SpeechT5Processor.from_pretrained("microsoft/speecht5_tts")

model = SpeechT5ForTextToSpeech.from_pretrained("microsoft/speecht5_tts").to(device)
vocoder = SpeechT5HifiGan.from_pretrained("microsoft/speecht5_hifigan").to(device)

from datasets import load_dataset

embeddings_dataset = load_dataset("Matthijs/cmu-arctic-xvectors", split="validation")
speaker_embeddings = torch.tensor(embeddings_dataset[7306]["xvector"]).unsqueeze(0)


def synthesise(text):
    print("sintetizando respuesta")
    inputs = processor(text=text, return_tensors="pt")
    speech = model.generate_speech(
        inputs["input_ids"].to(device), speaker_embeddings.to(device), vocoder=vocoder
    )
    return speech.cpu()


#### facebook mms, no lo pude hacer funcionar

In [ ]:
%pwd
!git clone https://github.com/jaywalnut310/vits.git
!python --version
%cd vits/

!pip install Cython==0.29.21
!pip install librosa==0.8.0
!pip install phonemizer==2.2.1
!pip install scipy
!pip install numpy
!pip install torch
!pip install torchvision
!pip install matplotlib
!pip install Unidecode==1.1.1

%cd monotonic_align/
%mkdir monotonic_align
!python3 setup.py build_ext --inplace
%cd ../
%pwd

In [ ]:
%cd chat_otrosmodelos
%pwd

In [21]:
from tts import synthesize

In [13]:
pip install fairseq sentencepiece

228.60s - pydevd: Sending message related to process being replaced timed-out after 5 seconds


Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.6/9.6 MB 17.0 MB/s eta 0:00:0000:0100:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.9/118.9 KB 35.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 286.2/286.2 KB 19.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 123.8/123.8 KB 25.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 112.4/112.4 KB 31.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for fairseq: filename=fairseq-0.12.2-cp310-cp310-linux_x86_64.whl size=11291819 sha256=4118e3f9771ef60e2501205a92f3683459f17c18835a49a6a9ef5dee8b65de7f
  Stored in directory: /home/matias/.cache/pip/wheels/e4/35/55/9c66f65ec7c83fd6fbc2b9502a0ac81b2448a1196159dacc32
  Create

In [16]:
from fairseq.checkpoint_utils import load_model_ensemble_and_task_from_hf_hub
from fairseq.models.text_to_speech.hub_interface import TTSHubInterface
import IPython.display as ipd


models, cfg, task = load_model_ensemble_and_task_from_hf_hub(
    "facebook/tts_transformer-es-css10",
    arg_overrides={"vocoder": "hifigan", "fp16": False}
)
model = models[0]
TTSHubInterface.update_cfg_with_data_cfg(cfg, task.data_cfg)
generator = task.build_generator([model], cfg)

# text = "Había una vez."

# sample = TTSHubInterface.get_model_input(task, text)
# wav, rate = TTSHubInterface.get_prediction(task, model, generator, sample)

# ipd.Audio(wav, rate=rate)

def syn_facebookmms(text):
    sample = TTSHubInterface.get_model_input(task, text)
    wav,rate = TTSHubInterface.get_prediction(task, model, generator, sample)
    return wav,rate


Fetching 10 files: 100%|██████████| 10/10 [00:00<00:00, 56603.29it/s]
2023-09-27 16:24:41 | INFO | fairseq.tasks.speech_to_text | dictionary size (spm_char.txt): 107
2023-09-27 16:24:42 | INFO | fairseq.models.text_to_speech.vocoder | loaded HiFiGAN checkpoint from /home/matias/.cache/fairseq/models--facebook--tts_transformer-es-css10/snapshots/f52cf36f741df546bed60cdd5e6b71e0b85378c1/hifigan.bin
2023-09-27 16:24:42 | INFO | fairseq.models.text_to_speech.vocoder | loaded HiFiGAN checkpoint from /home/matias/.cache/fairseq/models--facebook--tts_transformer-es-css10/snapshots/f52cf36f741df546bed60cdd5e6b71e0b85378c1/hifigan.bin


In [18]:
audio, rate = syn_facebookmms("hola, cómo estás? yo estoy bien, gracias por preguntar")
Audio(audio, rate=rate)

#### suno, es muy pesado

In [ ]:
from transformers import AutoProcessor, AutoModel


processor = AutoProcessor.from_pretrained("suno/bark-small")
model = AutoModel.from_pretrained("suno/bark-small")

inputs = processor(
    text=["Hello, my name is Suno. And, uh — and I like pizza. [laughs] But I also have other interests such as playing tic tac toe."],
    return_tensors="pt",
)

speech_values = model.generate(**inputs, do_sample=True)

In [26]:
from IPython.display import Audio

sampling_rate = model.generation_config.sample_rate
Audio(speech_values.cpu().numpy().squeeze(), rate=sampling_rate)

In [41]:

from huggingface_hub import HfFolder
import json
import requests
API_URL = "https://api-inference.huggingface.co/models/suno/bark-small"
headers = {"Authorization": f"Bearer {HfFolder().get_token()}"}
def query(payload):
    data = json.dumps(payload)
    response = requests.request("POST", API_URL, headers=headers, data=data)
    return json.loads(response.content.decode("utf-8"))
data = query("Can you please let us know more details about your ")

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): api-inference.huggingface.co:443
DEBUG:urllib3.connectionpool:https://api-inference.huggingface.co:443 "POST /models/suno/bark-small HTTP/1.1" 503 89


In [43]:
import json
import requests

headers = {"Authorization": f"Bearer {HfFolder().get_token()}"}
API_URL = "https://api-inference.huggingface.co/models/gpt2"

def query(payload):
    response = requests.post(API_URL, headers=headers, json=payload)
    return response

output = query({"text_inputs": "This is a test"})

DEBUG:urllib3.connectionpool:Starting new HTTPS connection (1): api-inference.huggingface.co:443
DEBUG:urllib3.connectionpool:https://api-inference.huggingface.co:443 "POST /models/gpt2 HTTP/1.1" 500 None


In [ ]:

Audio(output, rate=16000, autoplay=True)

## Probar todo junto

In [19]:
from IPython.display import Audio
launch_fn()
transcription = transcribe_whisper()
response = query_chatgpt(transcription)
# audio = synthesise(response)
audio, rate = syn_facebookmms(response)

Audio(audio, rate=rate, autoplay=True)

Listening for wake word...
Start speaking...
Preguntando  ¿Cómo hacer el color amariche?


In [29]:
def answer_question(filepath):
    transcription = transcribe_speech(filepath)
    response = query_chatgpt(transcription)
    # audio = synthesise(response)
    audio, rate = syn_facebookmms(response)
    return rate,audio

In [30]:
rate, audio = answer_question("como es el dia?")
Audio(audio,rate)




FileNotFoundError: [Errno 2] No such file or directory: 'como es el dia?'

In [28]:
import gradio as gr
with gr.Blocks() as demo:
    entrada = gr.Audio(source="microphone",type="filepath")
    salida = gr.Audio()
    boton = gr.Button("Responder")
    boton.click(answer_question,entrada,salida)
demo.launch(debug=True)

Running on local URL:  http://127.0.0.1:7862

To create a public link, set `share=True` in `launch()`.


/home/matias/.local/lib/python3.10/site-packages/gradio/processing_utils.py:188: UserWarning: Trying to convert audio automatically from int32 to 16-bit int format.
  warnings.warn(warning.format(data.dtype))


Preguntando  ¿Cuántos años tienen centenaria?


Traceback (most recent call last):
  File "/home/matias/.local/lib/python3.10/site-packages/gradio/routes.py", line 488, in run_predict
    output = await app.get_blocks().process_api(
  File "/home/matias/.local/lib/python3.10/site-packages/gradio/blocks.py", line 1434, in process_api
    data = self.postprocess_data(fn_index, result["prediction"], state)
  File "/home/matias/.local/lib/python3.10/site-packages/gradio/blocks.py", line 1335, in postprocess_data
    prediction_value = block.postprocess(prediction_value)
  File "/home/matias/.local/lib/python3.10/site-packages/gradio/components/audio.py", line 349, in postprocess
    file_path = self.audio_to_temp_file(
  File "/home/matias/.local/lib/python3.10/site-packages/gradio/components/base.py", line 325, in audio_to_temp_file
    temp_dir = Path(self.DEFAULT_TEMP_DIR) / self.hash_bytes(data.tobytes())
AttributeError: 'Tensor' object has no attribute 'tobytes'


Keyboard interruption in main thread... closing server.
